# Cluster Analysis
<br>
## Task

* Group the facebook posts into groups so that the groups contain posts with similar content.
* This task has no unique solution - the data is not labled so we don't know the correct answer therefore you will not be able to verify how good your model is

## Data
* We prepared two datasets about facebook pages
* The first dataset contains list of pages
* The second dataset contains for each page 100 randomly selected posts
* You will actualy not need to use the pages set unless you come up with some interesting features that will be useful

## Notes
* Create vector reprezentation for the texts
* Split the text to words
* Compute IDF
* Use KMeans algorithm to train a model

## About K-Means
* K-means is a unsupervised learning algorithm that can be used to cluster data into groups
* For details see <a target="_blank" href="https://en.wikipedia.org/wiki/K-means_clustering">wiki</a>

## Documentation
<br>
* Pyspark documentation of DataFrame API is <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.sql.html">here</a>

* Pyspark documentation of ML Pipelines library is <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.ml.html">here</a>

* Prezentation slides are accessed <a target="_blank" href = "https://docs.google.com/presentation/d/1XNKIfE5Atj_Mzse0wjmbwLecmVs2YkWm9cqOLqDVWPo/edit?usp=sharing">here</a>

### Import functions

In [4]:
from pyspark.sql.functions import col, count, desc, row_number, collect_list, length, array_contains, size
from pyspark.sql.functions import col, count, desc, array_contains, broadcast, explode, length, first, when

from pyspark.sql import Window

from pyspark.ml.feature import Tokenizer, StopWordsRemover, HashingTF, IDF, Normalizer, SQLTransformer

from pyspark.ml.clustering import KMeans

from pyspark.ml import Pipeline

import random

### Load the data

In [6]:
pages = spark.table('mlprague.facebook_pages')

posts = spark.table('mlprague.facebook_posts')

### You may want to do some exploratory analytics first

hint:
* see how many records you have
* what is the schema of the dataset
* see some records
* use can use printSchema(), show(), count(), or proprietaray function display()

In [8]:
pages.count()

Out[ 3 ]: 4718

In [9]:
posts.count()

Out[ 4 ]: 471800

In [10]:
display(pages)

page_id name description 1404160529823912 The Cannabist The Cannabist is The Denver Post's home for ideas, people, art, food and news, centered around the culture of cannabis. www.thecannabist.co 474226972647323 Alibabuy Réalisez vos rêves de voyage avec le comparateur Alibabuy. Bons plans, actualités et évasion, on vous aide à organiser vos futures vacances. 87076260498 ICING Icing is the one-stop shop for trendsetting jewelry & accessories at unbeatable prices! 54971236771 NASA - National Aeronautics and Space Administration Explore the universe and discover our home planet with the official NASA page on Facebook. Visit us at www.nasa.gov 152967154570 ARB 4x4 Accessories - USA Office ARB is a the manufacturer of quality off road accessories including air locking differentials, air compressors, winch bumpers, suspension systems, roof racks, skid plates, side rails, rear bumpers, roof top tents and recovery gear. 156195289363 Ram Trucks Welcome to the official Ram Trucks Facebook page. 
Visit us at www.RamTrucks.com

Standard operating hours: 
Mon – Fri 7:30 AM to 6:00 PM EST. 244456705578510 Nelnet Careers Catch a glimpse of what LifeAtNelnet is like. Like and subscribe to our page to receive job postings, company updates, and day-to-day shenanigans right in your feed. 307808202665938 Young Ford Morgan Young Ford in Morgan Utah is proud to be your wasatch front Ford dealer and meet all of your service, new car sales and used car sales needs! 104983900783 Já chci na pláž ... www.jachcinaplaz.cz, největší Facebooková stránka v ČR. Užijte si s námi dovolenou.
Stránka pro všechny, co nechtějí být na pláži sami. 108380356656 Atlanta Marriott Marquis Experience bustling energy and a stylish vibe at Atlanta Marriott Marquis. Our Atlanta hotel's location in Georgia is ideal, in Peachtree Center in the heart of downtown near the MARTA leading to top Atlanta attractions.
 126977607478401 Frontend Masters Master the most important JavaScript and front-end development skills such as React, Node.js, Vue, Functional JavaScript, CSS Grid, Flexbox and more! 171439799092 Riddell Sports Founded in 1929, Riddell is a premier designer and developer of protective sports equipment and a recognized leader in helmet technology and innovation. 244833777506 SAMHSA The Substance Abuse and Mental Health Services Administration (SAMHSA) leads public health efforts to advance the behavioral health of the nation. 48108221437 McCombs School of Business, The University of Texas at Austin Connecting you with the McCombs community. Official page of The University of Texas at Austin McCombs School of Business. 139269016237388 IRONMAN 70.3 Hawaii Swim with the Honu, ride on the IRONMAN World Championship bike course, and run in a vacationer's paradise. 

 267767893328038 Coast and Country Hotels Find us at www.coastandcountryhotels.com. Offering Weekend and Midweek breaks in England, Scotland and Wales. 274320942675899 U.S. Consulate General Alexandria - القنصلية العامة الأمريكية بالإسكندرية The U.S. Consulate General in Alexandria is a place where Americans and Egyptians meet. Please join our community to participate in discussions with us and keep up-to-date on our events and opportunities! 431315496941005 STAY Z STAY ZMRD - odpady ze dna internetových žump, zhovadilé události dní všedních i nevšedních a prezentace mravně zpustlých názorů na zavrženíhodná témata. 99203235257 Subaru UK Welcome to the official Facebook page for Subaru UK. We're here to help with any questions or queries, and make sure you give us a 'Like' to stay to up date with the latest news and exclusive competitions! 

 267848296697659 British Transport Police We are the national police force for the railways. Our aim is to keep you safe and make you feel secure while you travel. 186964441336268 Padres de San Diego Esta es la página oficial en Facebook de los Padres de San Diego en español. Escucha los partidos por XEMO 860 AM La Poderosa. Para más información, visita . 122396557792120 Safa

In [11]:
display(posts)

page_id message 240229921942 So, I think it's great you guys are making waves in the industry; including Bixby. However, I noticed you are extremely bias towards anything remotely conservative. This to me seems like a short fall to what could potentially be a great brand. It makes me wonder who you are, Like, who your team is. I wonder how a group of writers with so much going for them can be so bias and still feel like they are creative? I mean, how is it that I can be exposed to Flipboard for less then 3 minutes, and already know: your entire team does not support Trump; your entire team (much like AP) has an extremely progressive agenda; your entire team ONLY values progressive views; your entire team will NOT expose any good truths about any opposing views without constructing the narrative in such a way your paper still reads as if the opposing view is less good then your progressive agenda. I cant scroll down your news feed, which you managed to pitch of to Samsung's Bixby, without feeling a extremely bias narrative that onlky captures one side of the story. It's kind of like, have you ever noticed that AP ONLY posts pictures of Trump making a duck face. You see, it's not so much I am a huge Trump supporter, rather I bring it up as a metaphorical similarity to your Flipboard camp, and it scares me because, based on your boards, there is no doubt in my mind that your entire camp only has one point of view, which is damaging for any news business who wants to be deemed as credible. All of your stories, all of the news orginizations you post on, your entire flip board spells - Damn the president, loss faith in the system, fear big business, there are only good Democrates, the only good republicans are ones who side with Democrares, focus on black athletes, black talent, black calture, love imigrants, demand change and feel guilty if you happen to miss our message. 

I hear what you are saying, and a lot of what the progressives push for definetly has a place in our society. However, to completely disregard a very serious narrative told through a conservitives lense is extremely damaging. I mean the world isn't build so plainly, and relationships at the top arnt so black and white. Your demographic is a very young and vulnerable generation, your corrupting them and the youth by not capturing the story. Your helping to destroy due process, and frankly your making talk smack about your company to everyone I know. Which, i know it's like who the hell is this guy. You never know though. 6510408962 A quick throwback to Graduation last week... 
As well as celebrating the achievements of our students, we also formally welcomed our new chancellor, the incredibly inspiring Margaret Casely-Hayford. 66189885427 TAKE A SNACK BREAK! Popcorn, cookies & Candy! PopArt - 161 Valley Rd, Clifton. Opens 12pm M-F. Mention to Lisa you are from Montclaire State to receive a special deal! 422179114514548 If you know Simone, our office manager, then you'll know her beautiful handmade hats! Get your orders in ASAP! 106079664342 Three Film Fest Finalists are in the running for our $1,500 Grand Prize with less than a week left to win the public vote. This week we'll be sharing their messages to you, asking you to pick their film! First up is Jake Hatfield ( IES Abroad Tokyo | Penn State), and his film "Sapporo"!

Vote for Jake's film here: 446653042113846 TRIFIX i-SIZE je dokonale přizpůsobenaý potřebám dětí s výškou od 76 cm do 105 cm a je perfektním nástupcem jakékoliv dětské autosedačky.
bit.ly/trifix-i-size 153527691354397 Cardiff University Global Opportunities offer a range of opportunities for our students to study, work or volunteer abroad. Find out more about the reasons to study at cardiffuni ️ 190377228672 Lee ripped off his shirt and hopped up on the grooming table to show his dog that it wasn't that bad! 98888988071 Awesome! Congratulations to Donna and David on your new 2016 JEEP WRANGLER! Thank you again, Kunes Country Ford Lincoln of De

### Extract the features & construct the pipeline

hint
* do vector representation for the texts
 * use: 
 * <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.ml.html#pyspark.ml.feature.Tokenizer">Tokenizer</a> 
 * <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.ml.html#pyspark.ml.feature.StopWordsRemover">StopWordsRemover</a> 
 * <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.ml.html#pyspark.ml.feature.HashingTF">HashingTF</a> to compute term frequency and reduce the space or use the <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.ml.html#pyspark.ml.feature.CountVectorizer">CountVectorizer</a>
 * <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.ml.html#pyspark.ml.feature.IDF">IDF</a> 
 * <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.ml.html#pyspark.ml.feature.Normalizer">Normalizer</a> 
 * <a target="_blank" href="https://spark.apache.org/docs/latest/api/python/pyspark.ml.html#pyspark.ml.clustering.KMeans">KMeans</a> 
* See the slides 83, 84, 85, 101 in the presentation
* after you apply StopWordsRemover it is good to filter out rows with no (or very few) words. You can use the SQLTransformer defined bellow, that filters out all rows that have less than 10 words. This transformer assumes that the output column of StopWordsRemover is named 'noStopWords'. Just add this SQLTransformer to the pipeline right behind the StopwordsRemover

Note
* You may want to play with some input parameters: 
 * number of clusters for KMeans (try 4-8)
 * distanceMeasure for KMeans (default is 'euclidean' but you can try also 'cosine') 
 * numFeatures for HashingTF (try 1000)

In [13]:
# add this to the pipeline to remove empty or short messages

emptyRowsRemover = SQLTransformer(statement='SELECT * FROM __THIS__ where size(noStopWords) >= 10')

In [14]:
tokenizer = Tokenizer(inputCol='message', outputCol='words')

stopWordsRemover = StopWordsRemover(inputCol='words', outputCol='noStopWords')

hashingTF = HashingTF(numFeatures=1000, inputCol='noStopWords', outputCol='hashingTF')

idf = IDF(inputCol='hashingTF', outputCol='idf')

normalizer = Normalizer(inputCol='idf', outputCol='features')

kmeans = KMeans(featuresCol='features', predictionCol='prediction', k=5, seed=1)

pipeline = Pipeline(stages=[tokenizer, stopWordsRemover, emptyRowsRemover, hashingTF, idf, normalizer, kmeans])

model = pipeline.fit(posts)

### Apply the model on the data

hint
* just call transform, since the model is a transformer
* pass the training data as argument to the transform function

In [16]:
predictions = model.transform(posts)

### See how many pages are in your clusters

hint
* you can simply group by the column prediction and count
* the column with the cluster is called prediction by default

In [18]:
display(
  predictions
  .groupBy('prediction')
  .agg(count('*').alias('cnt'))
  .orderBy(desc('cnt'))
)

prediction cnt 1 288200 0 28766 2 21562 3 6768 4 3754

### See what pages are in your clusters

hint
* just filter the result for specific cluster:
 * filter(col('prediction') == 0) and so on for other clusters

In [20]:
display(
  predictions
  .filter(col('prediction') == 0)
)

page_id message words noStopWords hashingTF idf features prediction 5882213990 Je veux faire partie de vos étudiants. S'il vous plaît, comment dois-je m'y prendre ? List(je, veux, faire, partie, de, vos, étudiants., s'il, vous, plaît,, comment, dois-je, m'y, prendre, ?) List(je, veux, faire, partie, de, vos, étudiants., s'il, vous, plaît,, comment, dois-je, m'y, prendre, ?) List(0, 1000, List(39, 145, 175, 228, 281, 294, 573, 640, 667, 681, 745, 755, 779, 841, 976), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(0, 1000, List(39, 145, 175, 228, 281, 294, 573, 640, 667, 681, 745, 755, 779, 841, 976), List(3.091922368003184, 3.1960780135991707, 4.140699654446765, 3.9583480897007006, 2.050513023711846, 3.3676482761238886, 4.111074428044981, 3.738239898122811, 4.19167080525024, 3.7151518798351018, 2.6219660525186645, 3.8696751780955942, 2.6643302550033408, 2.8823962213604877, 3.100411490887389)) List(0, 1000, List(39, 145, 175, 228, 281, 294, 573, 640, 667, 681, 745, 755, 779, 841, 976), List(0.23223863609667092, 0.24006191307325356, 0.31101377259213353, 0.2973170901899588, 0.1540169160950969, 0.2529487967077935, 0.30878858018600963, 0.28078445446315475, 0.3148422873910098, 0.27905028094935613, 0.19693955651349646, 0.2906567431311191, 0.20012159132335436, 0.21650083264259637, 0.2328762660516423)) 0 579407188770431 [Maxi Banque Populaire IX]
Le Maxi Banque Populaire IX sera mis à l'eau lundi à Lorient ! Ne ratez rien en restant connectés sur les réseaux sociaux de Voile Banque Populaire ! PassionVoile 
️ List([maxi, banque, populaire, ix], le, maxi, banque, populaire, ix, sera, mis, à, l'eau, lundi, à, lorient, !, ne, ratez, rien, en, restant, connectés, sur, les, réseaux, sociaux, de, voile, banque, populaire, !, passionvoile, , ️) List([maxi, banque, populaire, ix], le, maxi, banque, populaire, ix, sera, mis, à, l'eau, lundi, à, lorient, !, ne, ratez, rien, en, restant, connectés, sur, les, réseaux, sociaux, de, voile, banque, populaire, !, passionvoile, , ️) List(0, 1000, List(2, 3, 22, 25, 35, 38, 53, 56, 259, 281, 284, 372, 377, 410, 420, 451, 460, 489, 556, 669, 738, 772, 810, 825, 847, 871, 883, 951), List(1.0, 1.0, 2.0, 3.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(0, 1000, List(2, 3, 22, 25, 35, 38, 53, 56, 259, 281, 284, 372, 377, 410, 420, 451, 460, 489, 556, 669, 738, 772, 810, 825, 847, 871, 883, 951), List(3.8291772783786517, 2.3574385638229733, 6.421067435701964, 6.586143824010502, 3.378763680358356, 4.91144421661795, 3.967088350283624, 3.43618413769408, 3.2711450220488736, 2.050513023711846, 3.5870173771991576, 0.692932335326463, 3.752792665261161, 3.475023971010344, 2.5919043690326036, 4.328509778496269, 2.7421472773601483, 4.515537611646647, 3.909879486175017, 4.120381721502938, 4.430664970094392, 2.4905117702516324, 11.306030293608941, 3.6562172665938975, 3.845260565182122, 3.2619055196995856, 3.993310814201236, 3.9581980634458245)) List(0, 1000, List(2, 3, 22, 25, 35, 38, 53, 56, 259, 281, 284, 372, 377, 410, 420, 451, 460, 489, 556, 669, 738, 772, 810, 825, 847, 871, 883, 951), List(0.1660131115748169, 0.10220621373070282, 0.2783839209147222, 0.28554077025292696, 0.14648553228900774, 0.2129345489776138, 0.17199221478762428, 0.14897498318076402, 0.141819749790416, 0.08889952661978266, 0.155514324036184, 0.030041924083248236, 0.16270147401453072, 0.15065887533647282, 0.11237142548533513, 0.18766155875510987, 0.11888517266657474, 0.19577010800084677, 0.16951193747219215, 0.178638214094997, 0.19209047389478887, 0.10797557238411407, 0.4901703765974236, 0.1585144695306016, 0.16671039882282984, 0.14141917326368555, 0.17312908375754682, 0.1716067784201128)) 0 214574018572873 Notre découverte du jour : un restaurant situé à Chelsea NYC
A essayer si vous allez à New-York. List(notre, découverte, du, jour, :, un, restaurant, situé, à, chelsea, nyc, a, essayer, si, vous, allez, à, new-york.) List(notr

In [21]:
display(
  predictions
  .filter(col('prediction') == 1)
)

page_id message words noStopWords hashingTF idf features prediction 6510408962 A quick throwback to Graduation last week... 
As well as celebrating the achievements of our students, we also formally welcomed our new chancellor, the incredibly inspiring Margaret Casely-Hayford. List(, a, quick, throwback, to, graduation, last, week..., , as, well, as, celebrating, the, achievements, of, our, students,, we, also, formally, welcomed, our, new, chancellor,, the, incredibly, inspiring, margaret, casely-hayford.) List(, quick, throwback, graduation, last, week..., , well, celebrating, achievements, students,, also, formally, welcomed, new, chancellor,, incredibly, inspiring, margaret, casely-hayford.) List(0, 1000, List(25, 39, 48, 54, 69, 84, 114, 120, 155, 157, 178, 263, 372, 612, 632, 789, 792, 959, 989), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(0, 1000, List(25, 39, 48, 54, 69, 84, 114, 120, 155, 157, 178, 263, 372, 612, 632, 789, 792, 959, 989), List(2.1953812746701673, 3.091922368003184, 3.8674806908618775, 4.047749280398138, 3.6294060091432407, 3.5300889859024323, 3.6702909938055592, 3.7706645897653606, 3.5984674866811264, 2.1630689403498136, 3.4226578739155817, 3.5180383055728277, 1.385864670652926, 3.963160852787954, 4.025841710532011, 3.8965327027873364, 2.7000064552320593, 2.4718452465817693, 2.690460552150776)) List(0, 1000, List(25, 39, 48, 54, 69, 84, 114, 120, 155, 157, 178, 263, 372, 612, 632, 789, 792, 959, 989), List(0.15134453662628009, 0.21315001793489216, 0.26661522525626663, 0.27904252727729595, 0.25020290416977586, 0.243356216974751, 0.25302142099420344, 0.2599409458828048, 0.24807007357676922, 0.14911699860295333, 0.23595016316055023, 0.24252547078430192, 0.09553832349153613, 0.2732111955954985, 0.27753226978888085, 0.2686180041510535, 0.18613223614948324, 0.17040332709952422, 0.18547416354260393)) 1 66189885427 TAKE A SNACK BREAK! Popcorn, cookies & Candy! PopArt - 161 Valley Rd, Clifton. Opens 12pm M-F. Mention to Lisa you are from Montclaire State to receive a special deal! List(take, a, snack, break!, popcorn,, cookies, &, candy!, popart, -, 161, valley, rd,, clifton., opens, 12pm, m-f., mention, to, lisa, you, are, from, montclaire, state, to, receive, a, special, deal!) List(take, snack, break!, popcorn,, cookies, &, candy!, popart, -, 161, valley, rd,, clifton., opens, 12pm, m-f., mention, lisa, montclaire, state, receive, special, deal!) List(0, 1000, List(3, 146, 148, 181, 313, 323, 334, 349, 429, 438, 499, 508, 562, 604, 609, 684, 743, 787, 817, 855, 860, 894), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0)) List(0, 1000, List(3, 146, 148, 181, 313, 323, 334, 349, 429, 438, 499, 508, 562, 604, 609, 684, 743, 787, 817, 855, 860, 894), List(2.3574385638229733, 3.3485499017618596, 3.7000894198052023, 3.8818317029920415, 3.8049478789518165, 4.184120750510544, 3.4400188059681924, 3.605822778851446, 3.6154662595088958, 3.859022250254804, 2.2295712966342998, 3.3184307716663834, 2.610557519489445, 3.6748005843115346, 3.922248405551794, 4.2780967323738155, 3.700205314804463, 8.42895056213772, 3.2818427455557644, 2.867014036198173, 2.9837459871580663, 3.818553531007595)) List(0, 1000, List(3, 146, 148, 181, 313, 323, 334, 349, 429, 438, 499, 508, 562, 604, 609, 684, 743, 787, 817, 855, 860, 894), List(0.1302641570208009, 0.18502964908138725, 0.20445454510207242, 0.2144970147883141, 0.21024867225212762, 0.23120049480934235, 0.19008391428384158, 0.19924568634008194, 0.19977855277311082, 0.21323664084749602, 0.12319864022367394, 0.18336536685902277, 0.14425066249834273, 0.203057168776694, 0.21673030636557955, 0.23639329272377418, 0.20446094907145398, 0.4657555689452644, 0.18134363511530097, 0.15842159041740517, 0.1648718069458584, 0.2110004750023508)) 1 422179114514548 If you know Simone, our office manager, then you'll know her beautiful handmade hats! Get your orders in ASAP! Lis

In [22]:
display(
  predictions
  .filter(col('prediction') == 2)
)

page_id message words noStopWords hashingTF idf features prediction 110427862329490 Une heure de sommeil gagnée ce week-end avec le passage à l'heure d'hiver : la raison parfaite pour venir passer cette longue nuit dans une de nos chambres et profitez de nos jardins colorés…

One more hour of sleep this weekend to enter Winter time: the perfect reason to spend this long night in our of our rooms and enjoy our colourful gardens… List(une, heure, de, sommeil, gagnée, ce, week-end, avec, le, passage, à, l'heure, d'hiver, :, la, raison, parfaite, pour, venir, passer, cette, longue, nuit, dans, une, de, nos, chambres, et, profitez, de, nos, jardins, colorés…, , one, more, hour, of, sleep, this, weekend, to, enter, winter, time:, the, perfect, reason, to, spend, this, long, night, in, our, of, our, rooms, and, enjoy, our, colourful, gardens…) List(une, heure, de, sommeil, gagnée, ce, week-end, avec, le, passage, à, l'heure, d'hiver, :, la, raison, parfaite, pour, venir, passer, cette, longue, nuit, dans, une, de, nos, chambres, et, profitez, de, nos, jardins, colorés…, , one, hour, sleep, weekend, enter, winter, time:, perfect, reason, spend, long, night, rooms, enjoy, colourful, gardens…) List(0, 1000, List(18, 44, 73, 76, 115, 134, 184, 215, 268, 281, 372, 384, 390, 394, 400, 410, 489, 527, 559, 566, 578, 590, 618, 678, 688, 690, 694, 700, 717, 772, 785, 786, 792, 813, 831, 835, 881, 889, 904, 908, 926, 931, 948, 953, 961, 998), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(0, 1000, List(18, 44, 73, 76, 115, 134, 184, 215, 268, 281, 372, 384, 390, 394, 400, 410, 489, 527, 559, 566, 578, 590, 618, 678, 688, 690, 694, 700, 717, 772, 785, 786, 792, 813, 831, 835, 881, 889, 904, 908, 926, 931, 948, 953, 961, 998), List(3.7668167602800646, 2.475925497057267, 3.059950930807626, 3.564604322118547, 2.8646490767342616, 3.3148766866552717, 3.9289276811457117, 4.270687766603457, 4.072499318755467, 6.151539071135538, 0.692932335326463, 4.063291921323997, 3.0677407085978405, 3.3382476406970167, 4.185061395862566, 3.475023971010344, 2.2577688058233236, 3.367897642319437, 4.209448201649882, 4.772537119236797, 4.283274335324853, 2.9525883880397057, 4.211958582421762, 2.5009375814569688, 3.3145613784388805, 3.6131263307662893, 3.7579365835232057, 3.338005558791457, 4.104627851141388, 2.4905117702516324, 2.3934901619291846, 3.5141817639630744, 5.400012910464119, 3.1006023730818417, 3.4152215945143665, 7.239897315244388, 4.055655762040296, 3.919213940395525, 3.1862552309372094, 3.5672391027266888, 2.8541997653481443, 4.18186680515362, 4.021197615388808, 3.698236924196119, 4.141960802258275, 3.700205314804463)) List(0, 1000, List(18, 44, 73, 76, 115, 134, 184, 215, 268, 281, 372, 384, 390, 394, 400, 410, 489, 527, 559, 566, 578, 590, 618, 678, 688, 690, 694, 700, 717, 772, 785, 786, 792, 813, 831, 835, 881, 889, 904, 908, 926, 931, 948, 953, 961, 998), List(0.1467209411460437, 0.09643955155087475, 0.1191878737407516, 0.13884458263788838, 0.11158068877243348, 0.12911746394931597, 0.153035309057503, 0.16634717543583583, 0.15862755501278963, 0.23960804558662946, 0.026990345126866634, 0.158268918502807, 0.11949129267547405, 0.13002778388009775, 0.16301195036343558, 0.13535534643150296, 0.08794214987403522, 0.13118267842896342, 0.1639618386442753, 0.18589466447441116, 0.1668374337430823, 0.11500600498492436, 0.16405962026013968, 0.09741379500275842, 0.12910518240731272, 0.14073455903657145, 0.146375050179154, 0.1300183545695476, 0.1598789905907053, 0.09700770016735576, 0.09322862021988468, 0.13688057810611176, 0.21033541763395325, 0.12077128441586327, 0.13302598943840954, 0.2820005897537722, 0.15797148314872772, 0.1526569500144127, 0.1241075411854794, 0.1389472097405965, 0.11117367858360093, 0.16288751814779517, 0.15662930697489152, 0.14404969411327595, 0.16133314

In [23]:
display(
  predictions
  .filter(col('prediction') == 3)
)

page_id message words noStopWords hashingTF idf features prediction 303499083413372 Having FOMO? You don’t have too! We are giving away 2 wristbands to ACL weekend 2. Sign up at for more details.
.
.
.
.
elanparkside acl liveconnected leasetoday tourwithus 78752 List(having, fomo?, you, don’t, have, too!, we, are, giving, away, 2, wristbands, to, acl, weekend, 2., sign, up, at, , for, more, details., ., ., ., ., elanparkside, acl, liveconnected, leasetoday, tourwithus, 78752) List(fomo?, don’t, too!, giving, away, 2, wristbands, acl, weekend, 2., sign, , details., ., ., ., ., elanparkside, acl, liveconnected, leasetoday, tourwithus, 78752) List(0, 1000, List(26, 56, 157, 205, 245, 256, 372, 466, 486, 737, 756, 769, 786, 825, 841, 873, 964, 989, 992), List(1.0, 4.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0)) List(0, 1000, List(26, 56, 157, 205, 245, 256, 372, 466, 486, 737, 756, 769, 786, 825, 841, 873, 964, 989, 992), List(3.9920685780166445, 13.74473655077632, 2.1630689403498136, 4.3420707912155585, 3.3859327744463292, 3.8236545818960006, 0.692932335326463, 3.1228655497061975, 3.0921116364810843, 3.1665545560293524, 3.8486160478284943, 4.453296426325783, 3.5141817639630744, 3.6562172665938975, 2.8823962213604877, 6.729487178479817, 2.9096744113606685, 2.690460552150776, 3.8513085642639737)) List(0, 1000, List(26, 56, 157, 205, 245, 256, 372, 466, 486, 737, 756, 769, 786, 825, 841, 873, 964, 989, 992), List(0.19278719309348816, 0.6637684517809881, 0.10446012670577114, 0.20968969437583107, 0.1635153462000554, 0.18465405085025358, 0.033463473214599554, 0.15081115766686623, 0.14932597260768174, 0.15292101142651016, 0.18585950382747046, 0.21506106452488646, 0.16970881763543172, 0.17656807501958807, 0.1391982792979585, 0.32498413259781733, 0.14051561280063557, 0.12992921535320925, 0.1859895323266833)) 3 295886277206213 SNACK

For a post work out snack why not rustle up a bowl of bircher muesli. For a delicious and healthy recipe check out Jamie Oliver's tasty recipe: .

Photo: @lucasfitfrench

muesli birchermuesli foodinspo wellness healthy superfoods deepheat stayactive List(snack, , for, a, post, work, out, snack, why, not, rustle, up, a, bowl, of, bircher, muesli., for, a, delicious, and, healthy, recipe, check, out, jamie, oliver's, tasty, recipe:, ., , photo:, @lucasfitfrench, , muesli, birchermuesli, foodinspo, wellness, healthy, superfoods, deepheat, stayactive) List(snack, , post, work, snack, rustle, bowl, bircher, muesli., delicious, healthy, recipe, check, jamie, oliver's, tasty, recipe:, ., , photo:, @lucasfitfrench, , muesli, birchermuesli, foodinspo, wellness, healthy, superfoods, deepheat, stayactive) List(0, 1000, List(15, 43, 56, 126, 146, 295, 337, 372, 374, 387, 418, 437, 441, 465, 491, 506, 527, 532, 543, 568, 605, 615, 620, 861, 882, 973), List(1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0)) List(0, 1000, List(15, 43, 56, 126, 146, 295, 337, 372, 374, 387, 418, 437, 441, 465, 491, 506, 527, 532, 543, 568, 605, 615, 620, 861, 882, 973), List(3.70333956776203, 3.936972776830543, 3.43618413769408, 3.629082122500733, 6.697099803523719, 3.4463828304946675, 4.297494566583951, 2.078797005979389, 3.616851522663978, 3.844992612340219, 2.996623657996016, 3.891327654811639, 3.445484034820284, 3.8383170201264347, 4.322877181282239, 3.721643493071609, 3.367897642319437, 3.9390309957282654, 3.4834800916490103, 4.307868323210694, 2.697324404197966, 7.13549317629475, 3.7780290367048304, 3.8522526603621507, 2.9993227149651807, 3.6984682985608717)) List(0, 1000, List(15, 43, 56, 126, 146, 295, 337, 372, 374, 387, 418, 437, 441, 465, 491, 506, 527, 532, 543, 568, 605, 615, 620, 861, 882, 973), List(0.18236853501013092, 0.19387364959331468, 0.1692126405775456, 0.17871177568301325, 0.32979429988466497, 0.1697148685345097, 0.21162730934650106, 0.10236899901485576, 0.17810948779293137, 0.18934414654851878, 0.1

In [24]:
display(
  predictions
  .filter(col('prediction') == 4)
)

page_id message words noStopWords hashingTF idf features prediction 240229921942 So, I think it's great you guys are making waves in the industry; including Bixby. However, I noticed you are extremely bias towards anything remotely conservative. This to me seems like a short fall to what could potentially be a great brand. It makes me wonder who you are, Like, who your team is. I wonder how a group of writers with so much going for them can be so bias and still feel like they are creative? I mean, how is it that I can be exposed to Flipboard for less then 3 minutes, and already know: your entire team does not support Trump; your entire team (much like AP) has an extremely progressive agenda; your entire team ONLY values progressive views; your entire team will NOT expose any good truths about any opposing views without constructing the narrative in such a way your paper still reads as if the opposing view is less good then your progressive agenda. I cant scroll down your news feed, which you managed to pitch of to Samsung's Bixby, without feeling a extremely bias narrative that onlky captures one side of the story. It's kind of like, have you ever noticed that AP ONLY posts pictures of Trump making a duck face. You see, it's not so much I am a huge Trump supporter, rather I bring it up as a metaphorical similarity to your Flipboard camp, and it scares me because, based on your boards, there is no doubt in my mind that your entire camp only has one point of view, which is damaging for any news business who wants to be deemed as credible. All of your stories, all of the news orginizations you post on, your entire flip board spells - Damn the president, loss faith in the system, fear big business, there are only good Democrates, the only good republicans are ones who side with Democrares, focus on black athletes, black talent, black calture, love imigrants, demand change and feel guilty if you happen to miss our message. 

I hear what you are saying, and a lot of what the progressives push for definetly has a place in our society. However, to completely disregard a very serious narrative told through a conservitives lense is extremely damaging. I mean the world isn't build so plainly, and relationships at the top arnt so black and white. Your demographic is a very young and vulnerable generation, your corrupting them and the youth by not capturing the story. Your helping to destroy due process, and frankly your making talk smack about your company to everyone I know. Which, i know it's like who the hell is this guy. You never know though. List(so,, i, think, it's, great, you, guys, are, making, waves, in, the, industry;, including, bixby., however,, i, noticed, you, are, extremely, bias, towards, anything, remotely, conservative., this, to, me, seems, like, a, short, fall, to, what, could, potentially, be, a, great, brand., it, makes, me, wonder, who, you, are,, like,, who, your, team, is., i, wonder, how, a, group, of, writers, with, so, much, going, for, them, can, be, so, bias, and, still, feel, like, they, are, creative?, i, mean,, how, is, it, that, i, can, be, exposed, to, flipboard, for, less, then, 3, minutes,, and, already, know:, your, entire, team, does, not, support, trump;, your, entire, team, (much, like, ap), has, an, extremely, progressive, agenda;, your, entire, team, only, values, progressive, views;, your, entire, team, will, not, expose, any, good, truths, about, any, opposing, views, without, constructing, the, narrative, in, such, a, way, your, paper, still, reads, as, if, the, opposing, view, is, less, good, then, your, progressive, agenda., i, cant, scroll, down, your, news, feed,, which, you, managed, to, pitch, of, to, samsung's, bixby,, without, feeling, a, extremely, bias, narrative, that, onlky, captures, one, side, of, the, story., it's, kind, of, like,, have, you, ever, noticed, that, ap, only, posts, pictures, of, trump, making, a, duck, face., you, see,, it's, not, so, much, i, am, a, huge, trump,

After playing a little bit with the data and input parameters to the learning algorithms, you might be able to identify that the data gets clustered according to language (with some error of course). By looking at some posts try to identify which clusters belong to english language and save it to a table. You can use this result as input in the next notebook where you will do LDA.

In [26]:
# we generate random string for the table name to avoid collisions
table_name = ''.join([random.choice('abcdefghijklmnoprstuvwxy') for _ in range(20)])

(
  predictions
  .select('page_id', 'message')
  .filter(col('prediction').isin([4])) # here write the number of clusters that belong to english language
  .repartition(32)
  .write
  .mode('overwrite')
  .saveAsTable(table_name)
)

print(table_name)

fuinstsmrlmpfysimfvk